TWITTER CALLS With api's

In [1]:
import tweepy
from textblob import TextBlob
import yaml
import csv
import sys
def get_api_access():
    """
    gets an authenticated twitter api accessor object

    Returns:
       api: authenticated twitter api accessor object
    """
    consumer_key= 'veneAQratcFrRq3XOznlYkO8F'
    consumer_secret= 'A3uNhrjLd3IznIorNGBLDb3q3z4IGS15bcgiTt8EZWxYSGBCFl'
    access_token= '150169370-swQZ4WsoJVZuM0Y6V0gVeS9KK50WdMnlSM0Udt9F'
    access_token_secret= 'SepQLvZuCa2JEOhui9t8ldVhOxJnXb2WmLiGQMPQzkUPb'
    auth = tweepy.OAuthHandler(consumer_key, consumer_secret)
    auth.set_access_token(access_token, access_token_secret)
    api = tweepy.API(auth)
    return api

def show_recent_tweets(api,topicname):
    public_tweets = api.search(q=topicname)
    print(len(public_tweets))
    for tweet in public_tweets:
        print(tweet.text)
        analysis = TextBlob(tweet.text)
        print(analysis.sentiment)
    return public_tweets

def get_tweets(self, query, count =10):
    tweets =[]
    try:
        fetched_tweets = self.search(q = query, since = '2017-8-20', until='2017-10-20',count = count)
        for tweet in fetched_tweets:
            parsed_tweet = {}
            parsed_tweet['text'] = tweet.text
            parsed_tweet['sentiment'] = TextBlob(tweet.text)
            if tweet.retweet_count > 0:
                if parsed_tweet not in tweets:
                    tweets.append(parsed_tweet)
                else:
                    tweets.append(parsed_tweet)
        return tweets
    except tweepy.TweepError as e:
            print("Error : " + str(e))

In [2]:
api = get_api_access()
tweets = get_tweets(api,"Bitcoin")
print(tweets)

[]


TWITTER calls with Web Scrapping

In [4]:
import json
from datetime import datetime
from bs4 import BeautifulSoup
from coala_utils.decorators import generate_ordering

@generate_ordering('timestamp', 'id', 'text', 'user', 'replies', 'retweets', 'likes')
class Tweet:
    def __init__(self, user, id, timestamp, fullname, text, replies, retweets, likes):
        self.user = user
        self.id = id
        self.timestamp = timestamp
        self.fullname = fullname
        self.text = text
        self.replies = replies
        self.retweets = retweets
        self.likes = likes
    @classmethod
    def from_soup(cls, tweet):
        return cls(
            user=tweet.find('span', 'username').text[1:],
            id=tweet['data-item-id'],
            timestamp=datetime.utcfromtimestamp(
                int(tweet.find('span', '_timestamp')['data-time'])),
            fullname=tweet.find('strong', 'fullname').text,
            text=tweet.find('p', 'tweet-text').text or "",
            replies = tweet.find('div', 'ProfileTweet-action--reply').find('span', 'ProfileTweet-actionCountForPresentation').text or '0',
            retweets = tweet.find('div', 'ProfileTweet-action--retweet').find('span', 'ProfileTweet-actionCountForPresentation').text or '0',
            likes = tweet.find('div', 'ProfileTweet-action--favorite').find('span', 'ProfileTweet-actionCountForPresentation').text or '0'
        )
    @classmethod
    def from_html(cls, html):
        #soup = BeautifulSoup(html, "lxml")
        soup = BeautifulSoup(html, "html5lib")
        tweets = soup.find_all('li', 'js-stream-item')
        if tweets:
            for tweet in tweets:
                try:
                    yield cls.from_soup(tweet)
                except AttributeError:
                    pass  # Incomplete info? Discard!
                

class JSONEncoder(json.JSONEncoder):
    def default(self, obj):
        if hasattr(obj, '__json__'):
            return obj.__json__()
        elif isinstance(obj, collections.Iterable):
            return list(obj)
        elif isinstance(obj, datetime):
            return obj.isoformat()
        elif hasattr(obj, '__getitem__') and hasattr(obj, 'keys'):
            return dict(obj)
        elif hasattr(obj, '__dict__'):
            return {member: getattr(obj, member)
                    for member in dir(obj)
                    if not member.startswith('_') and
                    not hasattr(getattr(obj, member), '__call__')}
        return json.JSONEncoder.default(self, obj)

In [2]:
import json
import logging
import random
import sys
from datetime import timedelta, date
from multiprocessing.pool import Pool
import requests
from fake_useragent import UserAgent

ua = UserAgent()
HEADERS_LIST = [ua.chrome, ua.google, ua['google chrome'], ua.firefox, ua.ff]
INIT_URL = "https://twitter.com/search?f=tweets&vertical=default&q={q}"
RELOAD_URL = "https://twitter.com/i/search/timeline?f=tweets&vertical=" \
             "default&include_available_features=1&include_entities=1&" \
             "reset_error_state=false&src=typd&max_position={pos}&q={q}"
        
        

def query_single_page(url, html_response=True, retry=3):
    """
    Returns tweets from the given URL.
    :param url: The URL to get the tweets from

    :param html_response: False, if the HTML is embedded in a JSON

    :param retry: Number of retries if something goes wrong.

    :return: The list of tweets, the pos argument for getting the next page.
    """
    headers = {'User-Agent': random.choice(HEADERS_LIST)}
    try:
        response = requests.get(url, headers=headers)
        if html_response:
            html = response.text
        else:
            json_resp = response.json()
            html = json_resp['items_html']
        #print(html)
        tweets = list(Tweet.from_html(html))
        if not tweets:
            return [], None
        if not html_response:
            return tweets, json_resp['min_position']
        return tweets, "TWEET-{}-{}".format(tweets[-1].id, tweets[0].id)
    except requests.exceptions.HTTPError as e:
        logging.exception('HTTPError {} while requesting "{}"'.format(e, url))
    except requests.exceptions.ConnectionError as e:
        logging.exception('ConnectionError {} while requesting "{}"'.format(e, url))
    except requests.exceptions.Timeout as e:
        logging.exception('TimeOut {} while requesting "{}"'.format(e, url))
    if retry > 0:
        logging.info("Retrying...")
        return query_single_page(url, html_response, retry-1)
    logging.error("Giving up.")
    return [], None

def query_tweets_once(query, limit=None, num_tweets=0):
    """
    Queries twitter for all the tweets you want! It will load all pages it gets
    from twitter. However, twitter might out of a sudden stop serving new pages,
    in that case, use the `query_tweets` method.
    Note that this function catches the KeyboardInterrupt so it can return
    tweets on incomplete queries if the user decides to abort.
    :param query: Any advanced query you want to do! Compile it at
                  https://twitter.com/search-advanced and just copy the query!
    :param limit: Scraping will be stopped when at least ``limit`` number of
                  items are fetched.
    :param num_tweets: Number of tweets fetched outside this function.
    :return:      A list of twitterscraper.Tweet objects. You will get at least
                  ``limit`` number of items.
    """
    logging.info("Querying {}".format(query))
    query = query.replace(' ', '%20').replace("#", "%23").replace(":", "%3A")
    pos = None
    tweets = []
    print(INIT_URL.format(q=query))
    try:
        while True:
            new_tweets, pos = query_single_page(
                INIT_URL.format(q=query) if pos is None
                else RELOAD_URL.format(q=query, pos=pos),
                pos is None
            )
            if len(new_tweets) == 0:
                logging.info("Got {} tweets for {}.".format(len(tweets), query))
                return tweets
            logging.info("Got {} tweets ({} new).".format(
                len(tweets) + num_tweets, len(new_tweets)))
            tweets += new_tweets
            if limit is not None and len(tweets) + num_tweets >= limit:
                return tweets
    except KeyboardInterrupt:
        logging.info("Program interrupted by user. Returning tweets gathered "
                     "so far...")
    except BaseException:
        logging.exception("An unknown error occurred! Returning tweets "
                          "gathered so far.")

    return tweets

def eliminate_duplicates(iterable):
    """
    Yields all unique elements of an iterable sorted. Elements are considered
    non unique if the equality comparison to another element is true. (In those
    cases, the set conversion isn't sufficient as it uses identity comparison.)
    """
    class NoElement: pass
    prev_elem = NoElement
    for elem in sorted(iterable):
        if prev_elem is NoElement:
            prev_elem = elem
            yield elem
            continue
        if prev_elem != elem:
            prev_elem = elem
            yield elem
def query_tweets(query, limit=None):
    tweets = []
    iteration = 1
    while limit is None or len(tweets) < limit:
        logging.info("Running iteration no {}, query is {}".format(
            iteration, repr(query)))
        new_tweets = query_tweets_once(query, limit, len(tweets))
        tweets.extend(new_tweets)
        if not new_tweets:
            break
        mindate = min(map(lambda tweet: tweet.timestamp, new_tweets)).date()
        maxdate = max(map(lambda tweet: tweet.timestamp, new_tweets)).date()
        logging.info("Got tweets ranging from {} to {}".format(mindate.isoformat(), maxdate.isoformat()))


        # Add a day, twitter only searches until excluding that day and we dont
        # have complete results for that one yet. However, we cannot limit the
        # search to less than one day: if all results are from the same day, we
        # want to continue searching further into the past: either there are no
        # further results or twitter stopped serving them and there's nothing
        # we can do.
        if mindate != maxdate:
            mindate += timedelta(days=1)
        # Twitter will always choose the more restrictive until:
        query += ' until:' + mindate.isoformat()
        iteration += 1
    # Eliminate duplicates
    return list(eliminate_duplicates(tweets))

def query_all_tweets(query):
    """
    Queries *all* tweets in the history of twitter for the given query. This
    will run in parallel for each ~10 days.
    :param query: A twitter advanced search query.
    :return: A list of tweets.
    """
    year = 2017
    month = 9
    limits = []
    while date(year=year, month=month, day=1) < date.today():
        nextmonth = month + 1 if month < 12 else 1
        nextyear = year + 1 if nextmonth == 1 else year
        limits.append(
            (date(year=year, month=month, day=1),
             date(year=year, month=month, day=10))
        )
        limits.append(
            (date(year=year, month=month, day=10),
             date(year=year, month=month, day=20))
        )
        limits.append(
            (date(year=year, month=month, day=20),
             date(year=nextyear, month=nextmonth, day=1))
        )
        print(year,month)
        year, month = nextyear, nextmonth
    queries = ['{} since:{} until:{}'.format(query, since, until)
               for since, until in reversed(limits)]
    pool = Pool(20)
    all_tweets = []
    try:
        #for new_tweets in pool.imap_unordered(query_tweets_once, queries):
        for new_tweets in queries:
            print(new_tweets)
            new_tweets = query_tweets_once(new_tweets)
            all_tweets.extend(new_tweets)
            logging.info("Got {} tweets ({} new).".format(
                len(all_tweets), len(new_tweets)))
    except KeyboardInterrupt:
        logging.info("Program interrupted by user. Returning all tweets "
                     "gathered so far.")
    return sorted(all_tweets)

In [3]:
import collections
import csv
row_elements = {'text': [], 'user': [], 'timestamp': []}
#tweets = query_tweets("bitcoin news", 10)[:10]
tweets = query_all_tweets("bitcoin news")
csv_file =  open('Tweets.csv', 'w',newline='')
writer = csv.DictWriter(csv_file,fieldnames=row_elements)
writer.writeheader()

for tweet in tweets:
    row_elements['text'] = tweet.text.encode('utf-8')
    row_elements['timestamp'] = tweet.timestamp
    row_elements['user'] = tweet.user
    writer.writerow(row_elements)
    print(row_elements)
    #data = {["text":text,"timestamp":timestamp,"user":user]}
    #dump(data, output, cls=JSONEncoder)
    #outfile.write('\n')
    #print(tweet.time.encode('utf-8'))
    
csv_file.close()
    

2017 9
2017 10
bitcoin news since:2017-10-20 until:2017-11-01
https://twitter.com/search?f=tweets&vertical=default&q=bitcoin%20news%20since%3A2017-10-20%20until%3A2017-11-01
bitcoin news since:2017-10-10 until:2017-10-20
https://twitter.com/search?f=tweets&vertical=default&q=bitcoin%20news%20since%3A2017-10-10%20until%3A2017-10-20
bitcoin news since:2017-10-01 until:2017-10-10
https://twitter.com/search?f=tweets&vertical=default&q=bitcoin%20news%20since%3A2017-10-01%20until%3A2017-10-10
bitcoin news since:2017-09-20 until:2017-10-01
https://twitter.com/search?f=tweets&vertical=default&q=bitcoin%20news%20since%3A2017-09-20%20until%3A2017-10-01


ERROR:root:An unknown error occurred! Returning tweets gathered so far.
Traceback (most recent call last):
  File "<ipython-input-2-7b039d500c78>", line 81, in query_tweets_once
    pos is None
  File "<ipython-input-2-7b039d500c78>", line 35, in query_single_page
    json_resp = response.json()
  File "D:\Python\Anaconda\envs\tensorflow\lib\site-packages\requests\models.py", line 892, in json
    return complexjson.loads(self.text, **kwargs)
  File "D:\Python\Anaconda\envs\tensorflow\lib\json\__init__.py", line 354, in loads
    return _default_decoder.decode(s)
  File "D:\Python\Anaconda\envs\tensorflow\lib\json\decoder.py", line 339, in decode
    obj, end = self.raw_decode(s, idx=_w(s, 0).end())
  File "D:\Python\Anaconda\envs\tensorflow\lib\json\decoder.py", line 357, in raw_decode
    raise JSONDecodeError("Expecting value", s, err.value) from None
json.decoder.JSONDecodeError: Expecting value: line 1 column 1 (char 0)


bitcoin news since:2017-09-10 until:2017-09-20
https://twitter.com/search?f=tweets&vertical=default&q=bitcoin%20news%20since%3A2017-09-10%20until%3A2017-09-20
bitcoin news since:2017-09-01 until:2017-09-10
https://twitter.com/search?f=tweets&vertical=default&q=bitcoin%20news%20since%3A2017-09-01%20until%3A2017-09-10
{'text': b'#Bitcoin #News:  Major Bitcoin Hardware Wallet Ledger Begins Monero Integration http://dlvr.it/PlFMsB\xc2\xa0pic.twitter.com/tTkuQPLLNO', 'user': 'Bank_Bit', 'timestamp': datetime.datetime(2017, 9, 6, 20, 5, 56)}
{'text': b'#Bitcoin #News:  Dentacoin\xe2\x80\x99s Unique Value http://dlvr.it/PlFMsS\xc2\xa0pic.twitter.com/r85yRdnzFw', 'user': 'Bank_Bit', 'timestamp': datetime.datetime(2017, 9, 6, 20, 5, 58)}
{'text': b'#Bitcoin #News:  Litecoin Retreats From All-Time Highs, But Is $100 in Reach? http://dlvr.it/PlFMsk\xc2\xa0', 'user': 'Bank_Bit', 'timestamp': datetime.datetime(2017, 9, 6, 20, 5, 58)}
{'text': b'#Bitcoin #News:  Historic Quarter: CoinDesk Launches Q

{'text': b'Monopoly Without a Monopolist: An Economic Analysis of the Bitcoin System [pdf] #Bitcoin #News #Headline http://ift.tt/2gAde4R\xc2\xa0', 'user': 'HeadlineBitcoin', 'timestamp': datetime.datetime(2017, 9, 7, 17, 57, 18)}
{'text': b'#bitcoin #btc $btc #Ethereum #eth $eth #OmiseGO #omg $omg #Golem #GNT $gnt\n\n2/16 PICS golem STREAM\n\nfollow me #news\n#cryptocurrency #icopic.twitter.com/wdVtdMFoZJ', 'user': 'bestcryptocoin', 'timestamp': datetime.datetime(2017, 9, 7, 17, 57, 25)}
{'text': b'#bitcoin #btc $btc #Ethereum #eth $eth #OmiseGO #omg $omg #Golem #GNT $gnt\n\n3/16 PICS golem STREAM\n\nfollow me #news\n#cryptocurrency #icopic.twitter.com/pH0JX1Glni', 'user': 'bestcryptocoin', 'timestamp': datetime.datetime(2017, 9, 7, 17, 57, 42)}
{'text': b'Canadian Securities Commission Grants Bitcoin Fund Manager Registration - Bitcoin News http://paper.li/dreamwonlife/1378670341?read=https%3A%2F%2Fnews.bitcoin.com%2Fcanadian%2Dsecurities%2Dcommission%2Dgrants%2Dbitcoin%2Dfund%2Dmana

{'text': b'Live look at what happens when you take a huge countdown off your website and follow it up with marginal news. #Komodo #bitcoin #Cryptopic.twitter.com/weSFhIcZoG', 'user': 'TheRoyalCrypto', 'timestamp': datetime.datetime(2017, 9, 8, 17, 34, 58)}
{'text': b'Markets Tumble Again \xe2\x80\x93 How Many Times can China Cry Wolf? https://news.bitcoin.com/how-many-times-can-china-cry-wolf/\xc2\xa0\xe2\x80\xa6 via @BTCTN', 'user': 'rdaccelerator1', 'timestamp': datetime.datetime(2017, 9, 8, 17, 34, 59)}
{'text': b'Daily Roundup - September 7, 2017 - Crypto Insider - #bitcoin and #blockchain News #fintech https://cryptoinsider.com/daily-roundup-september-7-2017\xc2\xa0\xe2\x80\xa6pic.twitter.com/D4EfVNIDcu', 'user': 'bitcoinagile', 'timestamp': datetime.datetime(2017, 9, 8, 17, 35, 1)}
{'text': b'Given how the pounding on the table said everything has been ready for YEARS to just wait on activation, a day is more than enough', 'user': 'Falkvinge', 'timestamp': datetime.datetime(2017,

...

{'text': b"It's Political: Why China Hates Bitcoin and Loves the Blockchain http://cur.lv/16q7v6\xc2\xa0 #google #news #blockchainpic.twitter.com/ys0hCggAhi", 'user': 'CryptoCurrent', 'timestamp': datetime.datetime(2017, 9, 27, 13, 15, 47)}
{'text': b'#bitcoin Price Is \xe2\x80\x98Like MMM Ponzi Scheme\xe2\x80\x99: Russian Economic Minister http://cur.lv/16q7v8\xc2\xa0 #cryptocurrency #breaking #news #discussion', 'user': 'CryptoCurrent', 'timestamp': datetime.datetime(2017, 9, 27, 13, 15, 48)}
{'text': b'#PuertoRico Suffers Physical #Cash Shortage After Power Grid Destroyed #bitcoin #economy #news https://bitsonline.com/puerto-rico-cash-shortage/\xc2\xa0\xe2\x80\xa6', 'user': 'bitsonlinecom', 'timestamp': datetime.datetime(2017, 9, 27, 13, 15, 57)}
{'text': b'It\xe2\x80\x99s Political: Why China Hates #bitcoin and Loves the #blockchain http://cur.lv/16q7vg\xc2\xa0 #cryptocurrency #breaking #news #discussion', 'user': 'CryptoCurrent', 'timestamp': datetime.datetime(2017, 9, 27, 13, 16,

{'text': b'Top 6 BTC/USD Exchange Orderbooks: Resistance til $4300:$18.1M; Support til $4000:$27.1M $BTC $BTCUSD #bitcoin #orderbook #trading #news', 'user': 'CryptoNewswire', 'timestamp': datetime.datetime(2017, 9, 28, 23, 0, 7)}
{'text': b'https://goo.gl/gWgzhH\xc2\xa0  << ARTICLE | SPECIAL PROMO >> https://rebrand.ly/ezinv024d\xc2\xa0\n#bitcoin #bitcoinnews #crypto #Japanpic.twitter.com/uBt3Od4TNw', 'user': 'LaylaMinx', 'timestamp': datetime.datetime(2017, 9, 28, 23, 1, 2)}
{'text': b'#REUTERS #BUSINESS  NEWS broadcast by #EMET_NEWS_PRESS: Backers withdraw two proposals to list U.S. bitcoin fun... http://ow.ly/Gzst50ejzZ1\xc2\xa0', 'user': 'emet_news_press', 'timestamp': datetime.datetime(2017, 9, 28, 23, 1, 5)}
{'text': b'Localbitcoins Trading Volume Sets New Global All-Time High #news #altcoin #bitcoin\n\nhttp://openlink.azurewebsites.net/aHR0cHM6Ly9uZXdzLmJpdGNvaW4uY29tL2xvY2FsYml0Y29pbnMtdHJhZGluZy12b2x1bWUtcmVhY2hlcy1uZXctZ2xvYmFsLXRpbWUtaGlnaC8=/aHR0cHM6Ly9uZXdzLmJpdGNvaW4uY29

{'text': b'South Korea Bans All Initial Coin Offerings - Bitcoin News https://news.bitcoin.com/south-korea-bans-initial-coin-offerings/\xc2\xa0\xe2\x80\xa6', 'user': 'Entail2', 'timestamp': datetime.datetime(2017, 9, 30, 1, 18, 36)}
{'text': b'South Korea Bans All Initial Coin Offerings - Bitcoin News https://news.bitcoin.com/south-korea-bans-initial-coin-offerings/\xc2\xa0\xe2\x80\xa6http://fb.me/I8IJPULf\xc2\xa0', 'user': 'Entail2', 'timestamp': datetime.datetime(2017, 9, 30, 1, 18, 42)}
{'text': b'I was wondering, if it possible for the goverments to starting buying BTC, rise the price increadibly and then become the new whales!!!!', 'user': 'cryptoctrade', 'timestamp': datetime.datetime(2017, 9, 30, 1, 19, 59)}
{'text': b'Cayman Investment Forum Focuses on Rise of Bitcoin and Failing Dollar - Bitcoin News http://fb.me/1mmZBYxVm\xc2\xa0', 'user': 'TavaresDavis88', 'timestamp': datetime.datetime(2017, 9, 30, 1, 21, 45)}
{'text': b"It could happen. Could already be happening? Who know

{'text': b'Brazil\xe2\x80\x99s Central Bank President Calls Bitcoin a Pyramid Scheme http://ift.tt/2inyAHn\xc2\xa0 #themerkle news', 'user': 'crypto_group', 'timestamp': datetime.datetime(2017, 10, 19, 17, 38, 26)}
{'text': b"#Cryptocurrency news: Who's bullish on #bitcoin and who's bashing? | #Payments NEXT http://ow.ly/vaPr30fZJuz\xc2\xa0pic.twitter.com/FmaKL508m4", 'user': 'Payments_Leader', 'timestamp': datetime.datetime(2017, 10, 19, 17, 40, 14)}
{'text': b'Goldman Sachs goes Bitcoin GOLD. https://www.bitcoins.gold\xc2\xa0', 'user': 'jpvandeloo', 'timestamp': datetime.datetime(2017, 10, 19, 17, 40, 33)}
{'text': b"#Bitcoin News Inspector General: US Mint Should Consider Bitcoin's Impact http://ow.ly/j4pr50eHvDy\xc2\xa0", 'user': 'BitcoinBlab', 'timestamp': datetime.datetime(2017, 10, 19, 17, 45, 26)}
{'text': b'#CBC #Elite8 Finishes Up: Which coin has a brighter future? $ZRX $WTC \n\n#Crypto #cryptocurrencies #cryptocurrency #altcoins #news #bitcoin', 'user': 'CryptoTelegram', 'ti

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.


CLEANUP TWEETS

In [9]:
import pandas as pd
import re as regex

class TwitterData_Initialize():
    data = []
    processed_data = []
    wordlist = []

    data_model = None
    data_labels = None
    is_testing = False

    def initialize(self, csv_file, is_testing_set=True, from_cached=None):
        if from_cached is not None:
            self.data_model = pd.read_csv(from_cached)
            return

        self.is_testing = is_testing_set

        if not is_testing_set:
            self.data = pd.read_csv(csv_file, header=0, names=["text", "user", "timestamp"])
            self.data = self.data[self.data["emotion"].isin(["positive", "negative", "neutral"])]
        else:
            self.data = pd.read_csv(csv_file, header=0, names=["text", "user","timestamp"],
                                    dtype={"text":"str","timestamp":"str","user":"str"},nrows=39850)
            not_null_text = 1 ^ pd.isnull(self.data["text"])
            not_null_id = 1 ^ pd.isnull(self.data["timestamp"])
            self.data = self.data.loc[not_null_id & not_null_text, :]

        self.processed_data = self.data
        self.wordlist = []
        self.data_model = None
        self.data_labels = None
        
class TwitterCleanuper:
    def iterate(self):
        for cleanup_method in [self.remove_urls,
                               self.remove_usernames,
                               self.remove_na,
                               self.remove_special_chars,
                               self.remove_numbers]:
            yield cleanup_method

    @staticmethod
    def remove_by_regex(tweets, regexp):
        tweets.loc[:, "text"].replace(regexp, "", inplace=True)
        return tweets

    def remove_urls(self, tweets):
        return TwitterCleanuper.remove_by_regex(tweets, regex.compile(r"http.?://[^\s]+[\s]?"))

    def remove_na(self, tweets):
        return tweets[tweets["text"] != "Not Available"]

    def remove_special_chars(self, tweets):  # it unrolls the hashtags to normal words
        for remove in map(lambda r: regex.compile(regex.escape(r)), [",", ":", "\"", "=", "&", ";", "%", "$",
                                                                     "@", "%", "^", "*", "(", ")", "{", "}",
                                                                     "[", "]", "|", "/", "\\", ">", "<", "-",
                                                                     "!", "?", ".", "'",
                                                                     "--", "---", "#"]):
            tweets.loc[:, "text"].replace(remove, "", inplace=True)
        return tweets

    def remove_usernames(self, tweets):
        return TwitterCleanuper.remove_by_regex(tweets, regex.compile(r"@[^\s]+[\s]?"))

    def remove_numbers(self, tweets):
        return TwitterCleanuper.remove_by_regex(tweets, regex.compile(r"\s?[0-9]+\.?[0-9]*"))
    
class TwitterData_Cleansing(TwitterData_Initialize):
    def __init__(self, previous):
        self.processed_data = previous.processed_data
        
    def cleanup(self, cleanuper):
        t = self.processed_data
        for cleanup_method in cleanuper.iterate():
            if not self.is_testing:
                t = cleanup_method(t)
            else:
                if cleanup_method.__name__ != "remove_na":
                    t = cleanup_method(t)

        self.processed_data = t
    

In [23]:
data = TwitterData_Initialize()
data.initialize("Tweets.csv")


text      user  \
0  b'#Bitcoin #News:  Major Bitcoin Hardware Wall...  Bank_Bit   
1  b'#Bitcoin #News:  Dentacoin\xe2\x80\x99s Uniq...  Bank_Bit   
2  b'#Bitcoin #News:  Litecoin Retreats From All-...  Bank_Bit   
3  b'#Bitcoin #News:  Historic Quarter: CoinDesk ...  Bank_Bit   
4  b'#Bitcoin #News:  Ethereum\xe2\x80\x99s Raide...  Bank_Bit   

             timestamp  
0  2017-09-06 20:05:56  
1  2017-09-06 20:05:58  
2  2017-09-06 20:05:58  
3  2017-09-06 20:05:59  
4  2017-09-06 20:05:59

In [12]:
data = TwitterData_Initialize()
data.initialize("Tweets.csv")
data = TwitterData_Cleansing(data)
data.cleanup(TwitterCleanuper())
#df.to_csv(file_name, encoding='utf-8', index=False)
#data.processed_data.head(5)
data.processed_data.to_csv("cleanedtweets.csv", encoding='utf-8', index=False)

copied the tweets from cleanedtweets to cleanedtweets01 as cleanedtweets was giving data error. Do not understand this behavious?

In [94]:
from textblob import TextBlob
import csv
from datetime import datetime
row_elements = {'timestamp': [], 'polarity': [], 'subjectivity': []}

csv_file_1 =  open('sentimentanalysis.csv', 'w',newline='')
#writer_1 = csv.writer(csv_file_1,dialect ='excel')
writer_1 = csv.DictWriter(csv_file_1,fieldnames=row_elements)
writer_1.writeheader()

with open("cleanedtweets01.csv", "r") as csvfile:
    data_list = csv.DictReader(csvfile, delimiter=',')
    for row in data_list:
        #date_time = str(row['timestamp'])
        date_time = row['timestamp'].replace("/", "").replace("-","")
        tweet = row['text']
        analysis = TextBlob(tweet)
        as_pol = analysis.sentiment[0]
        #as_subj = analysis.sentiment[1]
        if as_pol != 0.0:
            date_time= datetime.strptime(date_time, "%d%m%Y %H:%M")
            row_elements['timestamp'] = date_time
            row_elements['polarity'] = as_pol
            row_elements['subjectivity'] = analysis.sentiment[1]
            
            #date_time= datetime.strptime(date_time, "%Y%m%d %H:%M")
            #row_elements.append(date_time)
            #row_elements.append(as_pol)
            #row_elements.append(analysis.sentiment[1])
            #print(row_elements)
            writer_1.writerow(row_elements)
            #row_elements = []
        #print(as_pol)

csv_file_1.close()
        #data = TwitterData_Initialize()
#data.initialize("cleanedtweets.csv")

#analysis = TextBlob("my name is king and loving it")
#print(analysis.sentiment)
#print(data.processed_data.head(5))

Integrating Cryptocurrency exchanges

Match Sentiments data with Price